In [1]:
import torch
import pandas as pd
import os
from torch.utils.data import DataLoader, TensorDataset
from transformers import BertForSequenceClassification, BertTokenizer, TFBertModel, AdamW

2024-06-24 21:49:48.644385: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2024-06-24 21:49:49.569360: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT


In [2]:
to_train = pd.read_csv('/home/rpierson/PiersonREU/extracted/topic_zero_data.csv')
to_train

Issue_id Priority                                              Title  \
0          146       P3       UnknownHostException: Repositories (1GEWRWG)   
1          234       P3                              NPE in sync (1GJ4W10)   
2          217       P3                       UI BUG TO BE FILED (1GHQOGF)   
3         1749       P1  Debugger did not show source for type; and gen...   
4         1811       P3    Scripted Handler Example does not run (1GENWSM)   
...        ...      ...                                                ...   
2827    229022       P3  [Progress] Display#getShells returns disposed ...   
2828    229097       P3        NPE when using OpenCheatSheetFromHelpAction   
2829    229473       P3  [Contributions] ShowInMenu dispose is attempti...   
2830    229712       P3  NPE in MenuServiceFactory likely from File->Re...   
2831    229748       P3          Widget is disposed error in the .log file   

                                            Description        Component  \
0     UnknownHostException is not caught when the ho...             Team   
1     Did a sync of Eclipse UI.  It came up in the c...             Team   
2     While minimizing an Eclipse running in Eclipse...             Team   
3     There are two problems here:; problem 1:; - ra...               UI   
4     scripted handler example does not run in 116; ...        Scripting   
...                                                 ...              ...   
2827  I20080427-2000; ; To reproduce the latest I-Bu...               UI   
2828  Created attachment 97790; Demo project; ; Buil...  User Assistance   
2829  I20080429-0100; ; I got this by quitting Eclip...               UI   
2830  I found two of these in my .log.  I see restar...               UI   
2831  Using eclipse.buildId=I20080427-2000; java.ful...             Team   

                                          Combined_Text  Topic  
0     UnknownHostException: Repositories (1GEWRWG) U...      0  
1     NPE in sync (1GJ4W10) Did a sync of Eclipse UI...      0  
2     UI BUG TO BE FILED (1GHQOGF) While minimizing ...      0  
3     Debugger did not show source for type; and gen...      0  
4     Scripted Handler Example does not run (1GENWSM...      0  
...                                                 ...    ...  
2827  [Progress] Display#getShells returns disposed ...      0  
2828  NPE when using OpenCheatSheetFromHelpAction Cr...      0  
2829  [Contributions] ShowInMenu dispose is attempti...      0  
2830  NPE in MenuServiceFactory likely from File->Re...      0  
2831  Widget is disposed error in the .log file Usin...      0  

[2832 rows x 7 columns]

In [3]:
n = len(to_train)
split_index = int(.8 * n)
train_dataset = to_train.iloc[:split_index]
validation_dataset = to_train.drop(train_dataset.index)

In [4]:
topic_zero_train_data = pd.DataFrame(columns = ['Combined_Text'])
topic_zero_train_priority = pd.DataFrame(columns = ['Priority'])
topic_zero_validation_data = pd.DataFrame(columns = ['Combined_Text'])
topic_zero_validation_priority = pd.DataFrame(columns = ['Priority'])
topic_zero_train_data

Empty DataFrame
Columns: [Combined_Text]
Index: []

In [5]:
topic_zero_train_priority = train_dataset[['Priority']].copy()
topic_zero_train_data = train_dataset[['Combined_Text']].copy()
topic_zero_validation_priority['Priority'] = validation_dataset[['Priority']].copy()
topic_zero_validation_data = validation_dataset[['Combined_Text']].copy()
def extract_description(topic_zero_train_data):
    # Using regular expression to extract text after the first parentheses
    description_train = re.sub(r'^\([^)]+\)\s*', '', topic_zero_train_data)
    return description_train.strip()
def extract_description(topic_zero_validation_data):
    # Using regular expression to extract text after the first parentheses
    description_validate = re.sub(r'^\([^)]+\)\s*', '', topic_zero_validation_data)
    return description_validate.strip()
topic_zero_train_data

Combined_Text
0     UnknownHostException: Repositories (1GEWRWG) U...
1     NPE in sync (1GJ4W10) Did a sync of Eclipse UI...
2     UI BUG TO BE FILED (1GHQOGF) While minimizing ...
3     Debugger did not show source for type; and gen...
4     Scripted Handler Example does not run (1GENWSM...
...                                                 ...
2260  [Viewers] IllegalArgumentException opening Pac...
2261  SWT_AWT.new_Shell() unimplemented in OS X/Carb...
2262  [variables] NPE in details pane of the variabl...
2263  PHP IDE -> new project = stack Hi;; ; I am una...
2264  [rulers] BadLocationExceptions over empty rule...

[2265 rows x 1 columns]

In [6]:
topic_zero_train_data['Combined_Text'].dtypes

dtype('O')

In [7]:
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
model = BertForSequenceClassification.from_pretrained('bert-base-uncased', num_labels = 5)

/home/rpierson/anaconda3/envs/firstenvi/lib/python3.11/site-packages/huggingface_hub/file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [8]:
# Check for CUDA availability
if torch.cuda.is_available():
    print("CUDA is available. Number of GPUs:", torch.cuda.device_count())
    print("CUDA device name:", torch.cuda.get_device_name(5))
else:
    print("CUDA is not available.")
torch.cuda.set_device(torch.device("cuda:5"))
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
model.to(device)

CUDA is available. Number of GPUs: 8
CUDA device name: NVIDIA GeForce GTX 1080 Ti


BertForSequenceClassification(
  (bert): BertModel(
    (embeddings): BertEmbeddings(
      (word_embeddings): Embedding(30522, 768, padding_idx=0)
      (position_embeddings): Embedding(512, 768)
      (token_type_embeddings): Embedding(2, 768)
      (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (encoder): BertEncoder(
      (layer): ModuleList(
        (0-11): 12 x BertLayer(
          (attention): BertAttention(
            (self): BertSelfAttention(
              (query): Linear(in_features=768, out_features=768, bias=True)
              (key): Linear(in_features=768, out_features=768, bias=True)
              (value): Linear(in_features=768, out_features=768, bias=True)
              (dropout): Dropout(p=0.1, inplace=False)
            )
            (output): BertSelfOutput(
              (dense): Linear(in_features=768, out_features=768, bias=True)
              (LayerNorm): LayerNorm((768,), eps=1e-12,

In [9]:
print(torch.cuda.current_device())

5


In [10]:
#topic_zero_train_data['Combined_Text'] = topic_zero_train_data['Combined_Text'].apply(str)
topic_zero_training = topic_zero_train_data['Combined_Text'].tolist()
#topic_zero_train_data['Combined_Text'] = topic_zero_train_data['Combined_Text'].to_string(index = False)
#type(topic_zero_train_data['Combined_Text'])
topic_zero_training

['UnknownHostException: Repositories (1GEWRWG) UnknownHostException is not caught when the host name is invalid; ; 1. in the Repositories view; New->CVS repository location; 2. put a garbage host name( e.g. eh? ); 3. complete the wizard.; 4. expand the Project Version; \tUHE is thrown.; ; Log: Wed Jun 06 12:51:50 EDT 2001; 4 org.eclipse.vcm.core 4 Cannot locate host eh?; java.net.UnknownHostException: eh?; \tat java.net.InetAddress.getAllByName0(InetAddress.java:585); \tat java.net.InetAddress.getAllByName0(InetAddress.java:554); \tat java.net.InetAddress.getByName(InetAddress.java:463); \tat java.net.Socket.<init>(Socket.java:112); \tat ; org.eclipse.vcm.internal.core.ccvs.client.PServerConnection.createSocket; (PServerConnection.java:140); \tat org.eclipse.vcm.internal.core.ccvs.client.PServerConnection.open; (PServerConnection.java:190); \tat org.eclipse.vcm.internal.core.ccvs.client.Connection.open; (Connection.java:224); \tat org.eclipse.vcm.internal.core.ccvs.client.Client.<init>

In [11]:
topic_zero_train_data['Combined_Text'].dtypes

dtype('O')

In [12]:
extract_dir = '/home/rpierson/PiersonREU/extracted'
topic_zero_path = os.path.join(extract_dir, 'topic_zero_train_data.csv')
topic_zero_train_data.to_csv(topic_zero_path, index = False)

In [13]:
#topic_zero_train_data = pd.read_csv('/home/rpierson/PiersonREU/extracted/topic_zero_train_data.csv')
#topic_zero_train_data
topic_zero_train_data

Combined_Text
0     UnknownHostException: Repositories (1GEWRWG) U...
1     NPE in sync (1GJ4W10) Did a sync of Eclipse UI...
2     UI BUG TO BE FILED (1GHQOGF) While minimizing ...
3     Debugger did not show source for type; and gen...
4     Scripted Handler Example does not run (1GENWSM...
...                                                 ...
2260  [Viewers] IllegalArgumentException opening Pac...
2261  SWT_AWT.new_Shell() unimplemented in OS X/Carb...
2262  [variables] NPE in details pane of the variabl...
2263  PHP IDE -> new project = stack Hi;; ; I am una...
2264  [rulers] BadLocationExceptions over empty rule...

[2265 rows x 1 columns]

In [14]:

tokenized_list = [tokenizer.encode_plus(text, max_length = 512, padding = 'max_length', truncation = True, return_tensors ='pt')
                  for text in topic_zero_train_data['Combined_Text']]

In [15]:
max_length = max(len(text) for text in topic_zero_train_data['Combined_Text'])
max_length

30089

In [16]:
topic_zero_train_priority

Priority
0          P3
1          P3
2          P3
3          P1
4          P3
...       ...
2260       P3
2261       P3
2262       P3
2263       P3
2264       P3

[2265 rows x 1 columns]

In [17]:
label_map = {'P1': 1, 'P2': 2, 'P3': 3, 'P4': 4, 'P5': 5}
topic_zero_train_priority['Priority'] = topic_zero_train_priority['Priority'].map(label_map)
topic_zero_train_priority

Priority
0            3
1            3
2            3
3            1
4            3
...        ...
2260         3
2261         3
2262         3
2263         3
2264         3

[2265 rows x 1 columns]

In [18]:
input_ids = torch.cat([encoding['input_ids'] for encoding in tokenized_list]).tolist()
attention_mask = torch.cat([encoding['attention_mask'] for encoding in tokenized_list]).tolist()

In [19]:
# Example: Convert priority to tensor
topic_zero_train_priority_tensor = torch.tensor(topic_zero_train_priority['Priority'].tolist())

In [20]:
input_ids_tensor = torch.tensor(input_ids)
attention_mask_tensor = torch.tensor(attention_mask)

In [21]:
input_ids = input_ids_tensor.to(torch.device('cuda'))  # Replace with your device if using CPU

# Ensure attention_mask is also on the same device as input_ids
attention_mask = attention_mask_tensor.to(torch.device('cuda'))  # Replace with your device if using CPU

# Ensure topic_zero_train_priority_tensor is on the same device as the model
topic_zero_train_priority_tensor = topic_zero_train_priority_tensor.to(torch.device('cuda'))  # Replace with your device if using CPU


In [22]:
print(input_ids.size())
print(attention_mask.size())
print(topic_zero_train_priority_tensor.size())

torch.Size([2265, 512])
torch.Size([2265, 512])
torch.Size([2265])


In [25]:
labels = topic_zero_train_priority_tensor

In [26]:
dataset = TensorDataset(input_ids, attention_mask, labels)

In [27]:
optimizer = AdamW(model.parameters(), lr=1e-5) 

/home/rpierson/anaconda3/envs/firstenvi/lib/python3.11/site-packages/transformers/optimization.py:429: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(


In [28]:
epochs = 20
batch_size = 100  # Adjust batch size as needed
dataloader = DataLoader(dataset, batch_size=batch_size, shuffle=True)
for batch in dataloader:
        optimizer.zero_grad()
        input_ids = batch[0].to(device)
        attention_mask = batch[1].to(device)
        labels = batch[2].to(device)
        outputs = model(input_ids=input_ids, attention_mask=attention_mask)
        loss = nn.CrossEntropyLoss()(outputs, labels)
        loss.backward()
        optimizer.step()
        scheduler.step()

OutOfMemoryError: CUDA out of memory. Tried to allocate 1.17 GiB. GPU  has a total capacity of 10.91 GiB of which 932.06 MiB is free. Including non-PyTorch memory, this process has 10.00 GiB memory in use. Of the allocated memory 9.67 GiB is allocated by PyTorch, and 176.43 MiB is reserved by PyTorch but unallocated. If reserved but unallocated memory is large try setting PYTORCH_CUDA_ALLOC_CONF=expandable_segments:True to avoid fragmentation.  See documentation for Memory Management  (https://pytorch.org/docs/stable/notes/cuda.html#environment-variables)

In [ ]:
encoded_input = tokenizer(text, return_tensors='tf')
output = model(encoded_input)